We will learn about how to read ADLS GEN2 from Databricks using service principle and also how to write back to ADLS Gen2 from Databricks

In [0]:
## Here i have hardcoded application ID and directory ID . We can add them as well in Azure Key Vault and access them here securely without exposing.

service_credential = dbutils.secrets.get(scope="databricks-scope-abhi",key="service-principle-value")

spark.conf.set("fs.azure.account.auth.type.abhisaitestsa.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.abhisaitestsa.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id.abhisaitestsa.dfs.core.windows.net", "bd9a6c06-8af1-44ca-86cc-9e579edda1b8")
spark.conf.set("fs.azure.account.oauth2.client.secret.abhisaitestsa.dfs.core.windows.net", service_credential)
spark.conf.set("fs.azure.account.oauth2.client.endpoint.abhisaitestsa.dfs.core.windows.net", "https://login.microsoftonline.com/d4d0fbf8-a93d-4af0-a91a-27703219bb79/oauth2/token")

In [0]:
dbutils.fs.ls("abfss://input@abhisaitestsa.dfs.core.windows.net/")

[FileInfo(path='abfss://input@abhisaitestsa.dfs.core.windows.net/customers_orders_data/', name='customers_orders_data/', size=0, modificationTime=1701271897000)]

In [0]:
order_df = spark.read.csv("abfss://input@abhisaitestsa.dfs.core.windows.net/customers_orders_data/orders.csv",header=True,inferSchema=True)

In [0]:
order_df.write.mode("overwrite").format("csv").save("abfss://output@abhisaitestsa.dfs.core.windows.net/")
order_df.write.mode("overwrite").format("parquet").save("abfss://parquetoutput@abhisaitestsa.dfs.core.windows.net/")
order_df.write.mode("overwrite").format("delta").save("abfss://deltaoutput@abhisaitestsa.dfs.core.windows.net/")

---------------------------------------------------------------------------
AttributeError                            Traceback (most recent call last)
File <command-2197376481594972>, line 3
      1 order_df.write.mode("overwrite").format("csv").save("abfss://output@abhisaitestsa.dfs.core.windows.net/")
      2 order_df.write.mode("overwrite").format("parquet").save("abfss://parquetoutput@abhisaitestsa.dfs.core.windows.net/")
----> 3 order_df.write.mode("overwrite").format("delta").save("abfss://deltaoutput@abhisaitestsa.dfs.core.windows.net/").saveAsTable("orders_tbl")

AttributeError: 'NoneType' object has no attribute 'saveAsTable'

In [0]:
order_df.write.mode("append").format("delta").save("abfss://deltaoutput@abhisaitestsa.dfs.core.windows.net/")

In [0]:
order_df.write.mode("append").format("delta").saveAsTable("orders")

In [0]:
%sql 

create table orders(order_id int,order_date timestamp,order_customer_id int,order_status string)
using delta
tblproperties (delta.enableChangeDataFeed=true)

In [0]:
%sql

show tables;

database tableName isTemporary default orders false default orders_tbl false

In [0]:
%sql

drop table orders

In [0]:
%sql
cache 
select * from orders_tbl

In [0]:
%sql
select count(*) from orders_tbl

count(1) 206643

In [0]:
%sql

select * from table_changes("orders",2)

order_id order_date order_customer_id order_status _change_type _commit_version _commit_timestamp 1 2013-07-25T00:00:00Z 11599 CLOSED insert 2 2023-11-29T18:33:36Z 2 2013-07-25T00:00:00Z 256 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 3 2013-07-25T00:00:00Z 12111 COMPLETE insert 2 2023-11-29T18:33:36Z 4 2013-07-25T00:00:00Z 8827 CLOSED insert 2 2023-11-29T18:33:36Z 5 2013-07-25T00:00:00Z 11318 COMPLETE insert 2 2023-11-29T18:33:36Z 6 2013-07-25T00:00:00Z 7130 COMPLETE insert 2 2023-11-29T18:33:36Z 7 2013-07-25T00:00:00Z 4530 COMPLETE insert 2 2023-11-29T18:33:36Z 8 2013-07-25T00:00:00Z 2911 PROCESSING insert 2 2023-11-29T18:33:36Z 9 2013-07-25T00:00:00Z 5657 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW insert 2 2023-11-29T18:33:36Z 12 2013-07-25T00:00:00Z 1837 CLOSED insert 2 2023-11-29T18:33:36Z 13 2013-07-25T00:00:00Z 9149 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 14 2013-07-25T00:00:00Z 9842 PROCESSING insert 2 2023-11-29T18:33:36Z 15 2013-07-25T00:00:00Z 2568 COMPLETE insert 2 2023-11-29T18:33:36Z 16 2013-07-25T00:00:00Z 7276 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 17 2013-07-25T00:00:00Z 2667 COMPLETE insert 2 2023-11-29T18:33:36Z 18 2013-07-25T00:00:00Z 1205 CLOSED insert 2 2023-11-29T18:33:36Z 19 2013-07-25T00:00:00Z 9488 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 20 2013-07-25T00:00:00Z 9198 PROCESSING insert 2 2023-11-29T18:33:36Z 21 2013-07-25T00:00:00Z 2711 PENDING insert 2 2023-11-29T18:33:36Z 22 2013-07-25T00:00:00Z 333 COMPLETE insert 2 2023-11-29T18:33:36Z 23 2013-07-25T00:00:00Z 4367 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 24 2013-07-25T00:00:00Z 11441 CLOSED insert 2 2023-11-29T18:33:36Z 25 2013-07-25T00:00:00Z 9503 CLOSED insert 2 2023-11-29T18:33:36Z 26 2013-07-25T00:00:00Z 7562 COMPLETE insert 2 2023-11-29T18:33:36Z 27 2013-07-25T00:00:00Z 3241 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 28 2013-07-25T00:00:00Z 656 COMPLETE insert 2 2023-11-29T18:33:36Z 29 2013-07-25T00:00:00Z 196 PROCESSING insert 2 2023-11-29T18:33:36Z 30 2013-07-25T00:00:00Z 10039 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 31 2013-07-25T00:00:00Z 6983 PAYMENT_REVIEW insert 2 2023-11-29T18:33:36Z 32 2013-07-25T00:00:00Z 3960 COMPLETE insert 2 2023-11-29T18:33:36Z 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 34 2013-07-25T00:00:00Z 4189 PROCESSING insert 2 2023-11-29T18:33:36Z 35 2013-07-25T00:00:00Z 4840 COMPLETE insert 2 2023-11-29T18:33:36Z 36 2013-07-25T00:00:00Z 5649 PENDING insert 2 2023-11-29T18:33:36Z 37 2013-07-25T00:00:00Z 5863 CLOSED insert 2 2023-11-29T18:33:36Z 38 2013-07-25T00:00:00Z 11586 PROCESSING insert 2 2023-11-29T18:33:36Z 39 2013-07-25T00:00:00Z 8214 PENDING insert 2 2023-11-29T18:33:36Z 40 2013-07-25T00:00:00Z 12092 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 41 2013-07-25T00:00:00Z 8136 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 42 2013-07-25T00:00:00Z 9776 PENDING insert 2 2023-11-29T18:33:36Z 43 2013-07-25T00:00:00Z 7776 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 44 2013-07-25T00:00:00Z 10500 PENDING insert 2 2023-11-29T18:33:36Z 45 2013-07-25T00:00:00Z 2636 COMPLETE insert 2 2023-11-29T18:33:36Z 46 2013-07-25T00:00:00Z 1549 ON_HOLD insert 2 2023-11-29T18:33:36Z 47 2013-07-25T00:00:00Z 8487 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 48 2013-07-25T00:00:00Z 12186 PROCESSING insert 2 2023-11-29T18:33:36Z 49 2013-07-25T00:00:00Z 1871 PENDING insert 2 2023-11-29T18:33:36Z 50 2013-07-25T00:00:00Z 5225 CANCELED insert 2 2023-11-29T18:33:36Z 51 2013-07-25T00:00:00Z 12271 CLOSED insert 2 2023-11-29T18:33:36Z 52 2013-07-25T00:00:00Z 5126 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 53 2013-07-25T00:00:00Z 4701 PROCESSING insert 2 2023-11-29T18:33:36Z 54 2013-07-25T00:00:00Z 10628 PENDING_PAYMENT insert 2 2023-11-29T18:33:36Z 55 2013-07-25T00:00:00Z 2052 PENDING insert 2 2023-11-29T18:33:36Z 56 2013-07-25T00:00:00Z 10519 COMPLETE insert 2 2

In [0]:
%sql

select * from table_changes("orders",0)

order_id order_date order_customer_id order_status _change_type _commit_version _commit_timestamp 1 2013-07-25T00:00:00Z 11599 CLOSED insert 1 2023-11-29T18:24:05Z 2 2013-07-25T00:00:00Z 256 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 3 2013-07-25T00:00:00Z 12111 COMPLETE insert 1 2023-11-29T18:24:05Z 4 2013-07-25T00:00:00Z 8827 CLOSED insert 1 2023-11-29T18:24:05Z 5 2013-07-25T00:00:00Z 11318 COMPLETE insert 1 2023-11-29T18:24:05Z 6 2013-07-25T00:00:00Z 7130 COMPLETE insert 1 2023-11-29T18:24:05Z 7 2013-07-25T00:00:00Z 4530 COMPLETE insert 1 2023-11-29T18:24:05Z 8 2013-07-25T00:00:00Z 2911 PROCESSING insert 1 2023-11-29T18:24:05Z 9 2013-07-25T00:00:00Z 5657 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 10 2013-07-25T00:00:00Z 5648 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 11 2013-07-25T00:00:00Z 918 PAYMENT_REVIEW insert 1 2023-11-29T18:24:05Z 12 2013-07-25T00:00:00Z 1837 CLOSED insert 1 2023-11-29T18:24:05Z 13 2013-07-25T00:00:00Z 9149 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 14 2013-07-25T00:00:00Z 9842 PROCESSING insert 1 2023-11-29T18:24:05Z 15 2013-07-25T00:00:00Z 2568 COMPLETE insert 1 2023-11-29T18:24:05Z 16 2013-07-25T00:00:00Z 7276 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 17 2013-07-25T00:00:00Z 2667 COMPLETE insert 1 2023-11-29T18:24:05Z 18 2013-07-25T00:00:00Z 1205 CLOSED insert 1 2023-11-29T18:24:05Z 19 2013-07-25T00:00:00Z 9488 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 20 2013-07-25T00:00:00Z 9198 PROCESSING insert 1 2023-11-29T18:24:05Z 21 2013-07-25T00:00:00Z 2711 PENDING insert 1 2023-11-29T18:24:05Z 22 2013-07-25T00:00:00Z 333 COMPLETE insert 1 2023-11-29T18:24:05Z 23 2013-07-25T00:00:00Z 4367 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 24 2013-07-25T00:00:00Z 11441 CLOSED insert 1 2023-11-29T18:24:05Z 25 2013-07-25T00:00:00Z 9503 CLOSED insert 1 2023-11-29T18:24:05Z 26 2013-07-25T00:00:00Z 7562 COMPLETE insert 1 2023-11-29T18:24:05Z 27 2013-07-25T00:00:00Z 3241 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 28 2013-07-25T00:00:00Z 656 COMPLETE insert 1 2023-11-29T18:24:05Z 29 2013-07-25T00:00:00Z 196 PROCESSING insert 1 2023-11-29T18:24:05Z 30 2013-07-25T00:00:00Z 10039 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 31 2013-07-25T00:00:00Z 6983 PAYMENT_REVIEW insert 1 2023-11-29T18:24:05Z 32 2013-07-25T00:00:00Z 3960 COMPLETE insert 1 2023-11-29T18:24:05Z 33 2013-07-25T00:00:00Z 5793 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 34 2013-07-25T00:00:00Z 4189 PROCESSING insert 1 2023-11-29T18:24:05Z 35 2013-07-25T00:00:00Z 4840 COMPLETE insert 1 2023-11-29T18:24:05Z 36 2013-07-25T00:00:00Z 5649 PENDING insert 1 2023-11-29T18:24:05Z 37 2013-07-25T00:00:00Z 5863 CLOSED insert 1 2023-11-29T18:24:05Z 38 2013-07-25T00:00:00Z 11586 PROCESSING insert 1 2023-11-29T18:24:05Z 39 2013-07-25T00:00:00Z 8214 PENDING insert 1 2023-11-29T18:24:05Z 40 2013-07-25T00:00:00Z 12092 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 41 2013-07-25T00:00:00Z 8136 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 42 2013-07-25T00:00:00Z 9776 PENDING insert 1 2023-11-29T18:24:05Z 43 2013-07-25T00:00:00Z 7776 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 44 2013-07-25T00:00:00Z 10500 PENDING insert 1 2023-11-29T18:24:05Z 45 2013-07-25T00:00:00Z 2636 COMPLETE insert 1 2023-11-29T18:24:05Z 46 2013-07-25T00:00:00Z 1549 ON_HOLD insert 1 2023-11-29T18:24:05Z 47 2013-07-25T00:00:00Z 8487 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 48 2013-07-25T00:00:00Z 12186 PROCESSING insert 1 2023-11-29T18:24:05Z 49 2013-07-25T00:00:00Z 1871 PENDING insert 1 2023-11-29T18:24:05Z 50 2013-07-25T00:00:00Z 5225 CANCELED insert 1 2023-11-29T18:24:05Z 51 2013-07-25T00:00:00Z 12271 CLOSED insert 1 2023-11-29T18:24:05Z 52 2013-07-25T00:00:00Z 5126 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 53 2013-07-25T00:00:00Z 4701 PROCESSING insert 1 2023-11-29T18:24:05Z 54 2013-07-25T00:00:00Z 10628 PENDING_PAYMENT insert 1 2023-11-29T18:24:05Z 55 2013-07-25T00:00:00Z 2052 PENDING insert 1 2023-11-29T18:24:05Z 56 2013-07-25T00:00:00Z 10519 COMPLETE insert 1 2

In [0]:
%sql

alter table orders_tbl set TBLPROPERTIES(delta.enableChangeDataFeed=true)

In [0]:
%sql
update orders_tbl
set order_status = 'CLOSED' where 
order_id = 1

num_affected_rows 1

In [0]:
%sql
describe formatted orders

col_name data_type comment id int null date string null cus_id int null status string null # Detailed Table Information Catalog spark_catalog Database default Table orders Created Time Wed Nov 29 18:05:34 UTC 2023 Last Access UNKNOWN Created By Spark 3.4.1 Type MANAGED Location dbfs:/user/hive/warehouse/orders Provider delta Owner root Is_managed_location true Table Properties [delta.enableChangeDataFeed=true,delta.minReaderVersion=1,delta.minWriterVersion=4]